In [3]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
#importing the necessary modules
import pandas as pd
import numpy as np
import nltk
import string
import re
from nltk.corpus import stopwords
from nltk.tokenize import sent_tokenize,word_tokenize
import csv
import ast
import re
from nltk.corpus import wordnet
from nltk.corpus import sentiwordnet


In [5]:
%cd /content/drive/My Drive/NLP 2020/Project/Final

/content/drive/My Drive/NLP 2020/Project/Final


In [6]:
#opening and viewing dataset
data=pd.read_csv('Dataset_preprocessed.csv')
data

name  ... negative_words
0      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...              1
1      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...              0
2      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...              0
3      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...              1
4      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...              0
...                                                  ...  ...            ...
27402  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...              0
27403  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...              1
27404  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...              1
27405  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...              1
27406  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...              0

[27407 rows x 22 columns]

In [7]:
#checking the number of null values in each column of the dataframe
data.isnull().sum()

name                                               0
categories                                         0
reviews.doRecommend                                0
reviews.rating                                     0
reviews.text                                       0
reviews.title                                      0
Labels                                             0
mod_name_1                                         0
mod_name_2                                         0
Product_Name                                       0
review_without_trailing_leading_blank spaces       0
review_toLower                                     0
review_without_newline                             0
normalize                                          0
review_without_specialCharacters_alphaNumerical    1
removed_repetation_chars                           1
review_without_stopwords                           1
Feature_0                                          1
Feature_1                                     

In [8]:
#extracting the unique products for which reviews are given from the 'name' column and printing it
products=[]
for i in data['name']:
    #print(i)
    if i not in products:
        products.append(i)
for i in products:
    print(i)

All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta
Kindle Oasis E-reader with Leather Charging Cover - Merlot, 6 High-Resolution Display (300 ppi), Wi-Fi - Includes Special Offers,,
All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 32 GB - Includes Special Offers, Magenta
Fire HD 8 Tablet with Alexa, 8 HD Display, 32 GB, Tangerine - with Special Offers,
Amazon 5W USB Official OEM Charger and Power Adapter for Fire Tablets and Kindle eReaders,,,
Amazon 5W USB Official OEM Charger and Power Adapter for Fire Tablets and Kindle eReaders,,,
Amazon Kindle Fire Hd (3rd Generation) 8gb,,,
Amazon Kindle Fire Hd (3rd Generation) 8gb,,,
Fire Tablet, 7 Display, Wi-Fi, 8 GB - Includes Special Offers, Magenta
Kindle Oasis E-reader with Leather Charging Cover - Black, 6 High-Resolution Display (300 ppi), Wi-Fi - Includes Special Offers,,
Amazon - Kindle Voyage - 4GB - Wi-Fi + 3G - Black,,,
Amazon - Kindle Voyage - 4GB - Wi-Fi + 3G - Black,,,
Amazon - Kindle Voyage - 

In [9]:
#selecting only necessary columns from the original dataset and constructing a new dataset using those columns
new_data=data[['name', 'categories', 'reviews.doRecommend','reviews.rating','removed_repetation_chars','reviews.title']].copy()
new_data=new_data[new_data['removed_repetation_chars'].notna()] #dropping the rows for which the 'reviews.text' column is null
new_data=new_data[new_data['removed_repetation_chars'].notna()] #dropping the rows for which the 'reviews.rating' column is null
new_data

name  ...                            reviews.title
0      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...                                   Kindle
1      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...                                very fast
2      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  Beginner tablet for our 9 year old son.
3      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...                                  Good!!!
4      All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...                Fantastic Tablet for kids
...                                                  ...  ...                                      ...
27402  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...                  My new favorite product
27403  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...                     Lots of potential!!!
27404  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...            Good First Generation Product
27405  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...             Great for a "connected home"
27406  New Amazon Kindle Fire Hd 9w Powerfast Adapter...  ...                                 Cool toy

[27406 rows x 6 columns]

In [10]:
#checking the number of null values in each column of the new data set
new_data.isnull().sum()

name                        0
categories                  0
reviews.doRecommend         0
reviews.rating              0
removed_repetation_chars    0
reviews.title               0
dtype: int64

In [0]:
new_data.rename(columns = {'removed_repetation_chars':'reviews.text'}, inplace = True) 

In [12]:
#extracting the rows which correspond to the two products(kindle and fire tablet)
required_rows=[]
for index,row in new_data.iterrows():
    #print(row)
    if(row['name']=="Kindle Oasis E-reader with Leather Charging Cover - Merlot, 6 High-Resolution Display (300 ppi), Wi-Fi - Includes Special Offers,," or 
    row['name']=="All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta"):
        required_rows.append(row)
"""
for i in required_rows:
    print(i['name'])
"""
print(required_rows)
#creating a list of ratings of the required products
ratings=[]
for i in required_rows:
    ratings.append(i["reviews.rating"])
#print(ratings)

[name                   All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...
categories             Electronics,iPad & Tablets,All Tablets,Fire Ta...
reviews.doRecommend                                                    1
reviews.rating                                                         5
reviews.text           this product so far has not disappointed my ch...
reviews.title                                                     Kindle
Name: 0, dtype: object, name                   All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...
categories             Electronics,iPad & Tablets,All Tablets,Fire Ta...
reviews.doRecommend                                                    1
reviews.rating                                                         5
reviews.text           great for beginner or experienced person wooww...
reviews.title                                                  very fast
Name: 1, dtype: object, name                   All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...
ca

In [13]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [14]:
#printing list of stopwords
stopWords=set(stopwords.words('english'))
print(stopWords)

{'it', 'after', 'doing', 'how', 'she', "mustn't", 'those', 'weren', 'being', 'for', 'your', 'off', 'why', 'o', 'here', 'then', 's', 'a', 'by', "doesn't", 'its', 'are', "she's", 'as', "hasn't", 'her', 'such', "haven't", 'yourself', 't', 'mightn', 'where', 'does', "didn't", 'his', 'my', 'this', "it's", 'against', 'so', 'hadn', 'mustn', 'their', 'below', 'they', "you'd", 'itself', 'own', 'more', 'doesn', 'than', 'or', 'once', "wouldn't", "couldn't", 'very', 'up', 'ain', 'himself', 've', 'have', 'during', 'again', 'there', "should've", 'didn', 'too', 'an', 'with', 'to', 'no', 'won', "isn't", 'what', 'that', 'through', 'until', 'into', 're', 'will', 'few', 'was', "don't", "wasn't", "hadn't", 'isn', 'haven', 'and', 'had', 'hers', 'theirs', 'y', 'he', 'at', 'further', 'whom', 'them', 'i', "won't", 'm', 'am', 'of', 'd', 'we', 'wouldn', 'were', 'yourselves', 'aren', 'shan', 'the', "you've", 'has', "aren't", 'wasn', 'while', 'did', 'can', "you're", 'only', 'is', "shouldn't", 'themselves', 'other

In [15]:
#making a list that contains only the reviews
reviews=new_data["reviews.text"]
"""
for i in reviews:
    print(i)
    print("\n")
"""
reviews1=[] #list containing the reviews
tot=[] #list containing the product names
for i in required_rows:
    tot.append(i['name'])
    reviews1.append(i['reviews.text'])
for i in reviews1:
    print(i)
    print("\n")

Streaming output truncated to the last 5000 lines.

i love my kindle fire it has  it is is good for watching movies reading and anything you need a tablet for


we get this after my son broke his samsung tablet and i told was android operating system but wen the time to set it up came takes me a little lounger to make a new account password and paretal control for my kid but am happy that finally did it


this was a replacement for an amazon fire tablet this was a an up grade for my daughter who broke the screen on her old one she absolutely loved her old one she says the new one is even better


i bought this kindle fire for my teenage son so he could use it at school and play games on the kindle he loves it


you will not find another tablet like this with the affordable price


this tablet is small enough to pack but the screen is the perfect size for watching movies on the plane when traveling


love the ease of use with tablet have not had any issues


i highly recommend kindles i

In [16]:
print(tot)

['All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta'

In [18]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [19]:
#removal of stop words
#first we tokenize each review into individual words and check if the word is a stopword. If not we add it to sentence
#(i.e form a sentence using the words which are not stopwords)and append the sentence to the list tokenized_reviews
tokenized_reviews=list()
for review in reviews1:
    string=review
    #print("original:",string)
    words=word_tokenize(string)
    #print(words)
    sentence=" "
    for w in words:
        if w not in stopWords:
            sentence=sentence+' '+w
    tokenized_reviews.append(sentence)

for i in tokenized_reviews:
    print(i)
    

  product far disappointed children love use like ability monitor control content see ease
  great beginner experienced person wooww bought gift loves
  inexpensive tablet use learn step nabi thrilled learn skype already
  fire hd two weeks love tablet great valuewe prime members tablet shines love able easily access prime content well movies download watch laterthis screen really nice look nice crisp bright infact brighter ipad pro costing base model build fire insanely awesome running mm thick smooth glossy feel back really amazing hold like futuristic tab ur hands
  bought grand daughter comes visit set user entered age name amazon makes sure accesses sites content appropriate age simple loves capabilities also bought installed gig sd card gives little tablet plenty storage price think tablet best one spend hundreds dollars additional speed capacity comes basics tablets everything people ever need fraction cost
  amazon fire inch tablet perfect size purchased husband bigger screen p

In [20]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [21]:
#POS Tagging
#POS tagging each word in the reviews
from nltk import pos_tag
from nltk.corpus import treebank
from textblob import TextBlob
tagged_words=[] #list containing the POS tagged words of each review

for review in tokenized_reviews:
    word_list=[]
    data=TextBlob(review)
    tag=data.tags
    #print(tag)
    tagged_words.append(tag)
for i in tagged_words:
    print(i)

[('product', 'NN'), ('far', 'RB'), ('disappointed', 'JJ'), ('children', 'NNS'), ('love', 'VBP'), ('use', 'NN'), ('like', 'IN'), ('ability', 'NN'), ('monitor', 'NN'), ('control', 'NN'), ('content', 'NN'), ('see', 'VBP'), ('ease', 'NN')]
[('great', 'JJ'), ('beginner', 'NN'), ('experienced', 'VBD'), ('person', 'NN'), ('wooww', 'NNS'), ('bought', 'VBD'), ('gift', 'NN'), ('loves', 'NNS')]
[('inexpensive', 'JJ'), ('tablet', 'NN'), ('use', 'NN'), ('learn', 'JJ'), ('step', 'NN'), ('nabi', 'RB'), ('thrilled', 'VBD'), ('learn', 'JJ'), ('skype', 'NN'), ('already', 'RB')]
[('fire', 'NN'), ('hd', 'PRP'), ('two', 'CD'), ('weeks', 'NNS'), ('love', 'VBP'), ('tablet', 'RB'), ('great', 'JJ'), ('valuewe', 'JJ'), ('prime', 'JJ'), ('members', 'NNS'), ('tablet', 'VBP'), ('shines', 'NNS'), ('love', 'RBR'), ('able', 'JJ'), ('easily', 'RB'), ('access', 'NN'), ('prime', 'JJ'), ('content', 'NN'), ('well', 'RB'), ('movies', 'NNS'), ('download', 'VBP'), ('watch', 'VB'), ('laterthis', 'NN'), ('screen', 'NN'), ('rea

In [22]:
#this list contains the reviews and the POS tagging of the words in each review
ref_list=[]
for i in range(0,len(reviews1)):
    sub_list=[reviews1[i],tagged_words[i]]
    ref_list.append(sub_list)
for i in ref_list:
    print(i)
    print("\n")

Streaming output truncated to the last 5000 lines.

['i love my kindle fire it has  it is is good for watching movies reading and anything you need a tablet for', [('love', 'VB'), ('kindle', 'NN'), ('fire', 'NN'), ('good', 'JJ'), ('watching', 'NN'), ('movies', 'NNS'), ('reading', 'VBG'), ('anything', 'NN'), ('need', 'JJ'), ('tablet', 'NN')]]


['we get this after my son broke his samsung tablet and i told was android operating system but wen the time to set it up came takes me a little lounger to make a new account password and paretal control for my kid but am happy that finally did it', [('get', 'VB'), ('son', 'JJ'), ('broke', 'NN'), ('samsung', 'NN'), ('tablet', 'NN'), ('told', 'VBD'), ('android', 'RP'), ('operating', 'VBG'), ('system', 'NN'), ('wen', 'JJ'), ('time', 'NN'), ('set', 'VBN'), ('came', 'VBD'), ('takes', 'VBZ'), ('little', 'JJ'), ('lounger', 'JJR'), ('make', 'VB'), ('new', 'JJ'), ('account', 'NN'), ('password', 'JJ'), ('paretal', 'NN'), ('control', 'NN'), ('kid', 'NN'), 

In [23]:
#extracting aspects
#aspects can be a noun or a noun phrase.
prev_word=''
prev_tag=''
current_word=''
aspectList=[]
outputDict={}

for i in range(0,len(tagged_words)):
    sub_aspect=[]
    for word,tag in tagged_words[i]:
        if(tag=='NN' or tag=='NNP'): #if the word's tag is a noun,
            if(prev_tag=='NN' or prev_tag=='NNP'): #check if the next or consecutive word is also a noun
                current_word= prev_word + ' ' + word  #if yes, combine the two words to form one single word
            else:
                aspectList.append(prev_word.upper())
                sub_aspect.append(prev_word.upper())
                current_word= word
        prev_word=current_word
        prev_tag=tag
    ref_list[i].append(sub_aspect)
#Eliminating aspect which has 1 or less count
for aspect in aspectList:
        if(aspectList.count(aspect)>1):
                if(outputDict.keys()!=aspect):
                        outputDict[aspect]=aspectList.count(aspect)
#sorting the dictionary containing the aspect and the number of times it occurs in descending order
outputAspect=sorted(outputDict.items(), key=lambda x: x[1],reverse = True)
print(outputAspect)


[('TABLET', 586), ('PRICE', 256), ('USE', 247), ('FIRE', 134), ('PRODUCT', 122), ('SIZE', 95), ('SCREEN', 95), ('YEAR', 94), ('KINDLE', 85), ('BUY', 80), ('PURCHASE', 68), ('DEVICE', 66), ('TIME', 66), ('GIFT', 61), ('AMAZON', 54), ('FIRE HD', 54), ('SON', 52), ('EVERYTHING', 51), ('WIFE', 49), ('READING', 47), ('IPAD', 47), ('QUALITY', 46), ('THING', 43), ('VALUE', 42), ('LOVE', 41), ('DAY', 41), ('BATTERY LIFE', 41), ('SOMETHING', 40), ('DAUGHTER', 39), ('WAY', 38), ('APPS', 37), ('LIFE', 37), ('WORK', 37), ('LOT', 37), ('VERSION', 36), ('DEAL', 35), ('FRIDAY', 35), ('ACCESS', 34), ('CHARGE', 34), ('TABLET PRICE', 33), ('MONEY', 32), ('BATTERY', 32), ('CASE', 31), ('READER', 30), ('ANYONE', 29), ('INTERNET', 29), ('FIRE TABLET', 28), ('CHRISTMAS', 28), ('MUSIC', 27), ('WEB', 27), ('PICTURE', 26), ('MEMORY', 26), ('RESOLUTION', 26), ('WATCH', 25), ('ITEM', 25), ('STORAGE', 24), ('MOM', 24), ('SALE', 24), ('DISPLAY', 23), ('CARD', 22), ('PLAY', 22), ('STORE', 22), ('GET', 22), ('KINDLE

In [24]:
#inserting the name of the product in the reference list containg the review,POS tagged review and the list of 
#aspects in the review
for i in range(0,len(ref_list)):
    #print(i,tot[i])
    #print(ref_list[i])
    ref_list[i].insert(0, tot[i])

for i in ref_list:
    print(i)
    print("\n")


Streaming output truncated to the last 5000 lines.

['All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'i love my kindle fire it has  it is is good for watching movies reading and anything you need a tablet for', [('love', 'VB'), ('kindle', 'NN'), ('fire', 'NN'), ('good', 'JJ'), ('watching', 'NN'), ('movies', 'NNS'), ('reading', 'VBG'), ('anything', 'NN'), ('need', 'JJ'), ('tablet', 'NN')], ['USE', 'KINDLE FIRE', 'WATCHING', 'ANYTHING']]


['All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta', 'we get this after my son broke his samsung tablet and i told was android operating system but wen the time to set it up came takes me a little lounger to make a new account password and paretal control for my kid but am happy that finally did it', [('get', 'VB'), ('son', 'JJ'), ('broke', 'NN'), ('samsung', 'NN'), ('tablet', 'NN'), ('told', 'VBD'), ('android', 'RP'), ('operating', 'VBG'), ('system', 'NN'), ('wen', 'JJ')

In [25]:
#printing list of aspects
print(aspectList)

['', 'PRODUCT', 'USE', 'ABILITY MONITOR CONTROL CONTENT', 'EASE', 'BEGINNER', 'PERSON', 'GIFT', 'TABLET USE', 'STEP', 'SKYPE', 'FIRE', 'ACCESS', 'CONTENT', 'LATERTHIS SCREEN', 'LOOK', 'CRISP', 'INFACT BRIGHTER', 'BASE MODEL', 'FIRE', 'MM', 'FEEL', 'HOLD', 'TAB', 'DAUGHTER', 'USER', 'AGE NAME', 'AGE', 'GIG', 'CARD', 'PLENTY STORAGE PRICE', 'TABLET', 'SPEND', 'SPEED CAPACITY', 'EVERYTHING', 'FRACTION COST AMAZON FIRE INCH TABLET', 'SIZE', 'HUSBAND', 'PHONE', 'KNEW', 'PURCHASE', 'LIGHT', 'PRICE POINT', 'PURCHASE', 'GIFT INLAWS HUSBAND UNCLE', 'USE', 'DEVICE', 'TABLET BRAND', 'CHOICE', 'TIME', 'READER', 'WAY LOVE', 'OHH READER', 'PRODUCT', 'USE', 'SCREEN', 'FATHER', 'VALUE WATCH', 'USE', 'EVERYTHING NEED THANK YOUAND SILK', 'LOVE SIZE SCREEN', 'USE', 'BRILLIANT', 'READER', 'BARGAIN', 'TABLET', 'ANNOYING', 'VIDEO QUALITY', 'FUN', 'FAMILY', 'LOVE LOVE KINDLE FIRE YR', 'GRANDDAUGHTER', 'CHRISTMASWE', 'BESTLOVE FACT', 'MEMORY CARD', 'USE', 'TABLET', 'SCREEN', 'AMAZON', 'PLAY STORE', 'READING A

In [26]:
#creating a new dataframe whose rows are the name of the product, the review,POS tagged review, the list of
#aspects in the review and the rating of the product using the reference list(ref_list)
fin_data = pd.DataFrame(ref_list, columns = ['name', 'review','POS_tags','aspects']) 
fin_data['rating']=ratings
fin_data

name  ... rating
0     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...    5.0
1     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...    5.0
2     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...    5.0
3     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...    4.0
4     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...    5.0
...                                                 ...  ...    ...
2876  Kindle Oasis E-reader with Leather Charging Co...  ...    4.0
2877  Kindle Oasis E-reader with Leather Charging Co...  ...    5.0
2878  Kindle Oasis E-reader with Leather Charging Co...  ...    5.0
2879  Kindle Oasis E-reader with Leather Charging Co...  ...    5.0
2880  Kindle Oasis E-reader with Leather Charging Co...  ...    5.0

[2881 rows x 5 columns]

In [27]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to /root/nltk_data...


True

In [28]:
#classifier1
#SentimentIntensityAnalyzer belonging to the nltk.sentiment.vader module
#finding polarity of each individual review
import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer 
sentiments=[]
classifier= SentimentIntensityAnalyzer()
for sentence in reviews1:
        #print(sentence)
        ss = classifier.polarity_scores(sentence)
        sentiments.append(ss)
        #print(ss)
for i in sentiments:
    print(i)

/usr/local/lib/python3.6/dist-packages/nltk/twitter/__init__.py:20: UserWarning: The twython library has not been installed. Some functionality from the twitter package will not be available.
  warnings.warn("The twython library has not been installed. "


{'neg': 0.0, 'neu': 0.599, 'pos': 0.401, 'compound': 0.9194}
{'neg': 0.0, 'neu': 0.507, 'pos': 0.493, 'compound': 0.8934}
{'neg': 0.0, 'neu': 0.896, 'pos': 0.104, 'compound': 0.4404}
{'neg': 0.034, 'neu': 0.683, 'pos': 0.282, 'compound': 0.9881}
{'neg': 0.0, 'neu': 0.914, 'pos': 0.086, 'compound': 0.7876}
{'neg': 0.053, 'neu': 0.766, 'pos': 0.182, 'compound': 0.7096}
{'neg': 0.0, 'neu': 0.582, 'pos': 0.418, 'compound': 0.8885}
{'neg': 0.0, 'neu': 0.601, 'pos': 0.399, 'compound': 0.9231}
{'neg': 0.0, 'neu': 0.827, 'pos': 0.173, 'compound': 0.7615}
{'neg': 0.0, 'neu': 0.682, 'pos': 0.318, 'compound': 0.6369}
{'neg': 0.194, 'neu': 0.806, 'pos': 0.0, 'compound': -0.3412}
{'neg': 0.0, 'neu': 0.515, 'pos': 0.485, 'compound': 0.8555}
{'neg': 0.0, 'neu': 0.682, 'pos': 0.318, 'compound': 0.8799}
{'neg': 0.0, 'neu': 0.762, 'pos': 0.238, 'compound': 0.3612}
{'neg': 0.0, 'neu': 0.704, 'pos': 0.296, 'compound': 0.6369}
{'neg': 0.0, 'neu': 0.521, 'pos': 0.479, 'compound': 0.8481}
{'neg': 0.0, 'neu':

In [29]:
#adding the results of the classifier, i.e the sentiment of each review as a column in the dataframe
fin_data['classifier1']=sentiments
fin_data

name  ...                                        classifier1
0     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'neg': 0.0, 'neu': 0.599, 'pos': 0.401, 'comp...
1     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'neg': 0.0, 'neu': 0.507, 'pos': 0.493, 'comp...
2     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'neg': 0.0, 'neu': 0.896, 'pos': 0.104, 'comp...
3     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'neg': 0.034, 'neu': 0.683, 'pos': 0.282, 'co...
4     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'neg': 0.0, 'neu': 0.914, 'pos': 0.086, 'comp...
...                                                 ...  ...                                                ...
2876  Kindle Oasis E-reader with Leather Charging Co...  ...  {'neg': 0.013, 'neu': 0.828, 'pos': 0.159, 'co...
2877  Kindle Oasis E-reader with Leather Charging Co...  ...  {'neg': 0.039, 'neu': 0.705, 'pos': 0.256, 'co...
2878  Kindle Oasis E-reader with Leather Charging Co...  ...  {'neg': 0.027, 'neu': 0.836, 'pos': 0.137, 'co...
2879  Kindle Oasis E-reader with Leather Charging Co...  ...  {'neg': 0.0, 'neu': 0.691, 'pos': 0.309, 'comp...
2880  Kindle Oasis E-reader with Leather Charging Co...  ...  {'neg': 0.0, 'neu': 0.781, 'pos': 0.219, 'comp...

[2881 rows x 6 columns]

In [30]:
nltk.download('sentiwordnet')

[nltk_data] Downloading package sentiwordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/sentiwordnet.zip.


True

In [0]:
#classifier2
#using sentiwordnet from the nltk library
def sentiment(inputWord): 
    wordSynset=wordnet.synsets(inputWord)
    if(len(wordSynset) != 0):
        word=wordSynset[0].name()
        sentiment=sentiwordnet.senti_synset(word)
        if(sentiment.pos_score()>sentiment.neg_score()):
            return True
        elif(sentiment.pos_score()<sentiment.neg_score()):
            return False


In [32]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [37]:
#tokenizing each review into seperate words and finding its polarity using sentiwordnet
cl2=[]
for review in reviews1:
    string=review
    #print("original:",string)
    words=word_tokenize(string)
    #print(words)
    trf={}       #creating a seperate dictionary for each review which has the keys 'pos' and 'neg'
    trf['pos']=0 #the values are initialized to 0
    trf['neg']=0
    for w in words:
        #print(w)
        sen=sentiment(w) #checking orientation of each word in the review
        if(sen==True):
            trf['pos']+=1 #if the word is positive, increment 'pos' value in dictionary
        if(sen==False):
            trf['neg']+=1 #if the word is negative, increment 'neg' value in dictionary
    cl2.append(trf)       #append the dictionary to a list

print(cl2)


[{'pos': 3, 'neg': 3}, {'pos': 2, 'neg': 0}, {'pos': 2, 'neg': 1}, {'pos': 24, 'neg': 1}, {'pos': 13, 'neg': 3}, {'pos': 8, 'neg': 1}, {'pos': 1, 'neg': 1}, {'pos': 4, 'neg': 1}, {'pos': 5, 'neg': 1}, {'pos': 2, 'neg': 0}, {'pos': 1, 'neg': 1}, {'pos': 4, 'neg': 0}, {'pos': 6, 'neg': 0}, {'pos': 1, 'neg': 0}, {'pos': 2, 'neg': 1}, {'pos': 4, 'neg': 0}, {'pos': 1, 'neg': 0}, {'pos': 5, 'neg': 4}, {'pos': 3, 'neg': 1}, {'pos': 6, 'neg': 0}, {'pos': 5, 'neg': 0}, {'pos': 1, 'neg': 1}, {'pos': 5, 'neg': 0}, {'pos': 5, 'neg': 0}, {'pos': 5, 'neg': 1}, {'pos': 1, 'neg': 0}, {'pos': 1, 'neg': 1}, {'pos': 2, 'neg': 1}, {'pos': 2, 'neg': 0}, {'pos': 6, 'neg': 1}, {'pos': 3, 'neg': 0}, {'pos': 4, 'neg': 1}, {'pos': 2, 'neg': 0}, {'pos': 5, 'neg': 0}, {'pos': 1, 'neg': 1}, {'pos': 6, 'neg': 0}, {'pos': 0, 'neg': 0}, {'pos': 3, 'neg': 0}, {'pos': 1, 'neg': 2}, {'pos': 2, 'neg': 3}, {'pos': 9, 'neg': 2}, {'pos': 5, 'neg': 0}, {'pos': 2, 'neg': 2}, {'pos': 3, 'neg': 4}, {'pos': 3, 'neg': 0}, {'pos':

In [38]:
#adding the results of the sentiment analysis as a seperate column to the dataframe
fin_data['classifier2']=cl2
fin_data

name  ...            classifier2
0     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...   {'pos': 3, 'neg': 3}
1     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...   {'pos': 2, 'neg': 0}
2     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...   {'pos': 2, 'neg': 1}
3     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'pos': 24, 'neg': 1}
4     All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi,...  ...  {'pos': 13, 'neg': 3}
...                                                 ...  ...                    ...
2876  Kindle Oasis E-reader with Leather Charging Co...  ...  {'pos': 24, 'neg': 9}
2877  Kindle Oasis E-reader with Leather Charging Co...  ...  {'pos': 14, 'neg': 2}
2878  Kindle Oasis E-reader with Leather Charging Co...  ...  {'pos': 11, 'neg': 3}
2879  Kindle Oasis E-reader with Leather Charging Co...  ...   {'pos': 6, 'neg': 2}
2880  Kindle Oasis E-reader with Leather Charging Co...  ...   {'pos': 2, 'neg': 1}

[2881 rows x 7 columns]

In [39]:
#printing the review and the results of classifier1 and classifier2 for each review in the dataframe
for index,row in fin_data.iterrows():
    print(row['review'])
    print("classifier1:",row['classifier1'])
    print("classifier2:",row['classifier2'])
    print("\n")

Streaming output truncated to the last 5000 lines.
classifier1: {'neg': 0.069, 'neu': 0.627, 'pos': 0.305, 'compound': 0.9573}
classifier2: {'pos': 11, 'neg': 1}


for the low price it is very speedy and has sufficient storage spacewhile it does not have google play the amazon app store has most of the same apps or a workable alternatve
classifier1: {'neg': 0.119, 'neu': 0.832, 'pos': 0.049, 'compound': -0.3476}
classifier2: {'pos': 5, 'neg': 2}


we are really pleased with this tablet the color is great
classifier1: {'neg': 0.0, 'neu': 0.552, 'pos': 0.448, 'compound': 0.807}
classifier2: {'pos': 4, 'neg': 0}


at this price point it is very good but having being used ipad the display doesnt look sharp amazon app store lacks content overall good for my  yr old
classifier1: {'neg': 0.052, 'neu': 0.761, 'pos': 0.187, 'compound': 0.6817}
classifier2: {'pos': 6, 'neg': 0}


this is a great tablet i absolutely would recommend it to a friend i would buy it again
classifier1: {'neg': 0.0, 'ne

In [40]:
#positive or negative for each aspect
#counting the number of positive and negative reviews for each aspect
aspect_rating={}  #dictionary containing the aspect name and the no of positive and negative reviews for the aspect
for aspect,no in outputAspect:
    #print(aspect)
    aspect_rating[aspect]={"pos":0,"neg":0} #initializing  the no of positive and negative reviews to 0
#print(aspect_rating)
"""
for i in aspect_rating:
    for index,row in fin_data.iterrows():
        if i in row['aspects']:
            if row['classifier1']['compound']>0:
                aspect_rating[i]["pos"]+=1
            else:
                aspect_rating[i]["neg"]+=1
print(aspect_rating)
"""
#for each row in the dataser,for each aspect in the list of aspects for that row, if the aspect is present in the 
#dictionary aspect_rating, check the sentiment of the product from the "classifier1" column of that row
#if it is postive, increment the "pos" value in the dictionary else increment the "neg" value
for index,row in fin_data.iterrows():
    for i in row["aspects"]:
        if i in aspect_rating:
            if row["classifier1"]["compound"]>0:
                aspect_rating[i]["pos"]+=1
            else:
                aspect_rating[i]["neg"]+=1
#print(aspect_rating)
for i in aspect_rating:
    print(i,":","positive =>",aspect_rating[i]["pos"],",","negative =>",aspect_rating[i]["neg"])
    #print("\n")

TABLET : positive => 550 , negative => 36
PRICE : positive => 241 , negative => 15
USE : positive => 235 , negative => 12
FIRE : positive => 115 , negative => 19
PRODUCT : positive => 113 , negative => 9
SIZE : positive => 91 , negative => 4
SCREEN : positive => 87 , negative => 8
YEAR : positive => 91 , negative => 3
KINDLE : positive => 80 , negative => 5
BUY : positive => 75 , negative => 5
PURCHASE : positive => 60 , negative => 8
DEVICE : positive => 60 , negative => 6
TIME : positive => 62 , negative => 4
GIFT : positive => 58 , negative => 3
AMAZON : positive => 49 , negative => 5
FIRE HD : positive => 47 , negative => 7
SON : positive => 49 , negative => 3
EVERYTHING : positive => 45 , negative => 6
WIFE : positive => 45 , negative => 4
READING : positive => 45 , negative => 2
IPAD : positive => 42 , negative => 5
QUALITY : positive => 43 , negative => 3
THING : positive => 39 , negative => 4
VALUE : positive => 39 , negative => 3
LOVE : positive => 40 , negative => 1
DAY : pos

In [41]:
!pip3 install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz



     |████████████████████████████████| 12.0MB 343kB/s 
  Created wheel for en-core-web-sm: filename=en_core_web_sm-2.2.0-cp36-none-any.whl size=12019125 sha256=1e188ee57c1771eaf1184ea9d6ab12706900fa294b12015ab7f026f097197f18
  Stored in directory: /root/.cache/pip/wheels/48/5c/1c/15f9d02afc8221a668d2172446dd8467b20cdb9aef80a172a4
Successfully built en-core-web-sm
  Found existing installation: en-core-web-sm 2.2.5
    Uninstalling en-core-web-sm-2.2.5:
      Successfully uninstalled en-core-web-sm-2.2.5


In [44]:
!pip3 install -U spacy
!python3 -m spacy download en_core_web_sm
!pip3 install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz

Requirement already up-to-date: spacy in /usr/local/lib/python3.6/dist-packages (2.2.4)
     |████████████████████████████████| 12.0MB 599kB/s 
  Created wheel for en-core-web-sm: filename=en_core_web_sm-2.2.5-cp36-none-any.whl size=12011742 sha256=1cb8c68c18cf62888b179973cc45a6fd79f415308a01eca85e241055ed280445
  Stored in directory: /tmp/pip-ephem-wheel-cache-rzqn7405/wheels/6a/47/fb/6b5a0b8906d8e8779246c67d4658fd8a544d4a03a75520197a
Successfully built en-core-web-sm
  Found existing installation: en-core-web-sm 2.2.0
    Uninstalling en-core-web-sm-2.2.0:
      Successfully uninstalled en-core-web-sm-2.2.0
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')
  Using cached https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz
  Created wheel for en-core-web-sm: filename=en_core_web_sm-2.2.0-cp36-none-any.whl size=12019125 sha256=fbb9f2561b33568fc0c7710b0fdb290385e9515958774657c9a0c44

In [0]:
"""
import spacy
from tqdm import tqdm
nlp = spacy.load('en_core_web_lg', parse=True, tag=True, entity=True)
"""

"\nimport spacy\nfrom tqdm import tqdm\nnlp = spacy.load('en_core_web_lg', parse=True, tag=True, entity=True)\n"

In [0]:
#to view dependency of each word in a review
import spacy
import en_core_web_sm
diag= en_core_web_sm.load()

In [48]:
txt = 'easy to use and compact.'
fig1 = diag(txt)
spacy.displacy.render(fig1,style='dep',jupyter=True)

In [49]:
txt = 'I want good battery life'
fig2 = diag(txt)
spacy.displacy.render(fig2,style='dep',jupyter=True)

In [50]:
#recommendation based on user input
input1="i want nice hold case."
words=word_tokenize(input1) #tokenize the user input into seperate words and convert the words to uppercase
#print(words)
for i in range(0,len(words)):
    words[i]=words[i].upper()
#print(words)
j=0
#for each word in the input, if the word is present in the aspect_rating dictionary,
while(j<len(words)):
    if words[j] in aspect_rating:
        if((words[j]+" "+words[j+1]) in aspect_rating): #check if the next word is also present in the dictionary
            #print(j)
            aspect=words[j]+" "+words[j+1] #combine the 2 words into a single word and print its rating
            print(aspect,":","positive =>",aspect_rating[aspect]["pos"],",","negative =>",aspect_rating[aspect]["neg"])
            j=j+2
            #print(j)
        else:          
            #print(j)
            print(words[j],":","positive =>",aspect_rating[words[j]]["pos"],",","negative =>",aspect_rating[words[j]]["neg"])
    j=j+1
#if the aspect is present in the 'aspects' column of the review, recommend that product.
for index,row in fin_data.iterrows():
    if aspect in row['aspects']:
        print("Recommended product:",row['name'])
        break

WANT : positive => 2 , negative => 0
HOLD CASE : positive => 2 , negative => 0
Recommended product: Kindle Oasis E-reader with Leather Charging Cover - Merlot, 6 High-Resolution Display (300 ppi), Wi-Fi - Includes Special Offers,,


In [51]:
#recommendation based on user input
input1="i want good battery life."
words=word_tokenize(input1) #tokenize the user input into seperate words and convert the words to uppercase
#print(words)
for i in range(0,len(words)):
    words[i]=words[i].upper()
#print(words)
j=0
#for each word in the input, if the word is present in the aspect_rating dictionary,
while(j<len(words)):
    if words[j] in aspect_rating:
        if((words[j]+" "+words[j+1]) in aspect_rating): #check if the next word is also present in the dictionary
            #print(j)
            aspect=words[j]+" "+words[j+1] #combine the 2 words into a single word and print its rating
            print(aspect,":","positive =>",aspect_rating[aspect]["pos"],",","negative =>",aspect_rating[aspect]["neg"])
            j=j+2
            #print(j)
        else:          
            #print(j)
            print(words[j],":","positive =>",aspect_rating[words[j]]["pos"],",","negative =>",aspect_rating[words[j]]["neg"])
    j=j+1
#if the aspect is present in the 'aspects' column of the review, recommend that product.
for index,row in fin_data.iterrows():
    
    if aspect in row['aspects']:
        print("Recommended product:",row['name'])
        break

WANT : positive => 2 , negative => 0
GOOD : positive => 2 , negative => 0
BATTERY LIFE : positive => 38 , negative => 3
Recommended product: All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta


In [52]:
input2="easy to use and compact."
l1=[]
words=word_tokenize(input2)
#print(words)
for i in range(0,len(words)):
    words[i]=words[i].upper()
#print(words)
j=0
while(j<len(words)):
    if words[j] in aspect_rating:
        if((words[j]+" "+words[j+1]) in aspect_rating):
            #print(j)
            aspect=words[j]+" "+words[j+1]
            l1.append(aspect)
            print(aspect,":","positive =>",aspect_rating[aspect]["pos"],",","negative =>",aspect_rating[aspect]["neg"])
            j=j+2
            #print(j)
        else:
            #print(j)
            l1.append(words[j])
            print(words[j],":","positive =>",aspect_rating[words[j]]["pos"],",","negative =>",aspect_rating[words[j]]["neg"])
    j=j+1

#checking how many times the aspect occurs in the 'aspects' column of each product
#print(l1)
product_list={}
product_list["Kindle Oasis E-reader with Leather Charging Cover - Merlot, 6 High-Resolution Display (300 ppi), Wi-Fi - Includes Special Offers,,"]=0
product_list["All-New Fire HD 8 Tablet, 8 HD Display, Wi-Fi, 16 GB - Includes Special Offers, Magenta"]=0
#print(product_list)
i=0
while(i<len(l1)):
    aspect=l1[i]
    for index,row in fin_data.iterrows():
        #print(aspect)
        #print(row['aspects'])
        if aspect in row['aspects']:
            product_list[row['name']]+=1
    i=i+1
#print(product_list)


EASY : positive => 2 , negative => 0
USE : positive => 235 , negative => 12
COMPACT : positive => 2 , negative => 0
